In [49]:
# things we need for NLP
import nltk
from nltk.stem.lancaster import LancasterStemmer
stemmer = LancasterStemmer()

# things we need for Tensorflow
import numpy as np
import tflearn
import tensorflow as tf
import random

In [50]:
# import our chat-bot intents file
import json
with open('intents_noresponse.json') as json_data:
    intents = json.load(json_data)

In [51]:
intents

{u'intents': [{u'patterns': [u'Hi',
    u'How are you',
    u'Is anyone there?',
    u'Hello',
    u'Good day'],
   u'tag': u'greeting'},
  {u'patterns': [u'Bye', u'See you later', u'Goodbye'], u'tag': u'goodbye'},
  {u'patterns': [u'Thanks', u'Thank you', u"That's helpful"],
   u'tag': u'thanks'},
  {u'patterns': [u'What hours are you open?',
    u'What are your hours?',
    u'When are you open?'],
   u'tag': u'hours'},
  {u'patterns': [u'Which mopeds do you have?',
    u'What kinds of mopeds are there?',
    u'What do you rent?'],
   u'tag': u'mopeds'},
  {u'patterns': [u'Do you take credit cards?',
    u'Do you accept Mastercard?',
    u'Are you cash only?'],
   u'tag': u'payments'},
  {u'patterns': [u'Are you open today?',
    u'When do you open today?',
    u'What are your hours today?'],
   u'tag': u'opentoday'},
  {u'patterns': [u'Can we rent a moped?',
    u"I'd like to rent a moped",
    u'How does this work?'],
   u'tag': u'rental'},
  {u'patterns': [u'today', u'Today'], u'ta

In [52]:
words = []
classes = []
documents = []
ignore_words = ['?']
# loop through each sentence in our intents patterns
for intent in intents['intents']:
    for pattern in intent['patterns']:
        # tokenize each word in the sentence
        w = nltk.word_tokenize(pattern)
        # add to our words list
        words.extend(w)
        # add to documents in our corpus
        documents.append((w, intent['tag']))
        # add to our classes list
        if intent['tag'] not in classes:
            classes.append(intent['tag'])

# stem and lower each word and remove duplicates
words = [stemmer.stem(w.lower()) for w in words if w not in ignore_words]
words = sorted(list(set(words)))

# remove duplicates
classes = sorted(list(set(classes)))

print (len(documents), "documents")
print (len(classes), "classes", classes)
print (len(words), "unique stemmed words", words)

(31, 'documents')
(10, 'classes', [u'goodbye', u'greeting', u'hours', u'mopeds', u'not_today', u'opentoday', u'payments', u'rental', u'thanks', u'today'])
(52, 'unique stemmed words', [u"'d", u"'s", u'a', u'acceiv', u'anyon', u'ar', u'bye', u'can', u'card', u'cash', u'credit', u'day', u'do', u'doe', u'few', u'good', u'goodby', u'hav', u'hello', u'help', u'hi', u'hour', u'how', u'i', u'in', u'is', u'kind', u'lat', u'lik', u'mastercard', u'mop', u'of', u'on', u'op', u'rent', u'see', u'tak', u'thank', u'that', u'ther', u'thi', u'to', u'today', u'tomorrow', u'we', u'week', u'what', u'when', u'which', u'work', u'yo', u'you'])


In [53]:
# create our training data
training = []
output = []
# create an empty array for our output
output_empty = [0] * len(classes)

# training set, bag of words for each sentence
for doc in documents:
    # initialize our bag of words
    bag = []
    # list of tokenized words for the pattern
    pattern_words = doc[0]
    # stem each word
    pattern_words = [stemmer.stem(word.lower()) for word in pattern_words]
    # create our bag of words array
    for w in words:
        bag.append(1) if w in pattern_words else bag.append(0)

    # output is a '0' for each tag and '1' for current tag
    output_row = list(output_empty)
    output_row[classes.index(doc[1])] = 1

    training.append([bag, output_row])

# shuffle our features and turn into np.array
random.shuffle(training)
training = np.array(training)

# create train and test lists
train_x = list(training[:,0])
train_y = list(training[:,1])

In [54]:
# reset underlying graph data
tf.reset_default_graph()
# Build neural network
net = tflearn.input_data(shape=[None, len(train_x[0])])
net = tflearn.fully_connected(net, 8)
net = tflearn.fully_connected(net, 8)
net = tflearn.fully_connected(net, len(train_y[0]), activation='softmax')
net = tflearn.regression(net)

# Define model and setup tensorboard
model = tflearn.DNN(net, tensorboard_dir='tflearn_logs')
# Start training (apply gradient descent algorithm)
model.fit(train_x, train_y, n_epoch=1000, batch_size=8, show_metric=True)
model.save('model.tflearn')

Training Step: 3999  | total loss: 0.88961 | time: 0.009s
| Adam | epoch: 1000 | loss: 0.88961 - acc: 0.9106 -- iter: 24/31
Training Step: 4000  | total loss: 0.81523 | time: 0.012s
| Adam | epoch: 1000 | loss: 0.81523 - acc: 0.9196 -- iter: 31/31
--
INFO:tensorflow:/media/david13/OS/1_ai_dev/2_Chatbot_development/model.tflearn is not in all_model_checkpoint_paths. Manually adding it.


INFO:tensorflow:/media/david13/OS/1_ai_dev/2_Chatbot_development/model.tflearn is not in all_model_checkpoint_paths. Manually adding it.


In [55]:
def clean_up_sentence(sentence):
    # tokenize the pattern
    sentence_words = nltk.word_tokenize(sentence)
    # stem each word
    sentence_words = [stemmer.stem(word.lower()) for word in sentence_words]
    return sentence_words

# return bag of words array: 0 or 1 for each word in the bag that exists in the sentence
def bow(sentence, words, show_details=False):
    # tokenize the pattern
    sentence_words = clean_up_sentence(sentence)
    # bag of words
    bag = [0]*len(words)  
    for s in sentence_words:
        for i,w in enumerate(words):
            if w == s: 
                bag[i] = 1
                if show_details:
                    print ("found in bag: %s" % w)

    return(np.array(bag))

In [56]:
p = bow("is your shop open today?", words)
print (p)
print (classes)

[0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 0 1 0 0 0
 0 0 0 0 0 1 0 0 0 0 0 0 0 1 0]
[u'goodbye', u'greeting', u'hours', u'mopeds', u'not_today', u'opentoday', u'payments', u'rental', u'thanks', u'today']


In [57]:
print(model.predict([p]))

[[2.8185982e-03 5.2470237e-04 1.0449647e-02 2.0652367e-08 1.9319054e-06
  6.7586166e-01 3.3843905e-06 5.6646424e-08 1.5072611e-03 3.0883282e-01]]


In [58]:
# save all of our data structures
import pickle
pickle.dump( {'words':words, 'classes':classes, 'train_x':train_x, 'train_y':train_y}, open( "training_data", "wb" ) )

In [59]:
# create a data structure to hold user context
context = {}

ERROR_THRESHOLD = 0.25
def classify(sentence):
    # generate probabilities from the model
    results = model.predict([bow(sentence, words)])[0]
    # filter out predictions below a threshold
    results = [[i,r] for i,r in enumerate(results) if r>ERROR_THRESHOLD]
    # sort by strength of probability
    results.sort(key=lambda x: x[1], reverse=True)
    return_list = []
    
    
    for r in results:
        return_list.append((classes[r[0]], r[1]))
    # return tuple of intent and probability
    return return_list

def response(sentence, userID='123', show_details=False):
        results = classify(sentence)
        if results:
            # loop as long as there are matches to process
            while results:
                for i in intents['intents']:
                    # find a tag matching the first result
                    if i['tag'] == results[0][0]:
                        # set context for this intent if necessary
                        if 'context_set' in i:
                            if show_details: print ('context:', i['context_set'])
                            context[userID] = i['context_set']

                        # check if this intent is contextual and applies to this user's conversation
                        if not 'context_filter' in i or \
                            (userID in context and 'context_filter' in i and i['context_filter'] == context[userID]):
                            if show_details: print ('tag:', i['tag'])
                            # a random response from the intent
                            return random.choice(i['responses'])

                results.pop(0)

In [60]:
with open('dialog.json') as json_data:
    dialog = json.load(json_data)

In [33]:
dialog

{u'child_node': [{u'child_node': [],
   u'child_status': False,
   u'jump_status': True,
   u'jump_to': u'main_node',
   u'response_by': [u'Hello thanks for visiting',
    u'Good to see you again',
    u'Hi there, how can I help?'],
   u'tag': u'conversation_start',
   u'triggered_by': [u'greeting']},
  {u'child_node': [],
   u'child_status': False,
   u'jump_status': True,
   u'jump_to': u'main_node',
   u'response_by': [u"We're open everyday 9am-9pm",
    u'Our hours are 9am - 9pm everyday'],
   u'tag': u'operating_time',
   u'triggered_by': [u'hours']},
  {u'child_node': [],
   u'child_status': False,
   u'jump_status': True,
   u'jump_to': u'main_node',
   u'response_by': [u'We rent Yamaha, Piaggio and Vespa mopeds',
    u'We have Piaggio,Vespa and Yamaha mopeds'],
   u'tag': u'asking_rental_rental_type',
   u'triggered_by': [u'mopeds']},
  {u'child_node': [{u'child_node': [],
     u'child_status': False,
     u'jump_status': True,
     u'jump_to': u'main_node',
     u'response_by'

In [14]:
intents['intents']

[{u'patterns': [u'Hi',
   u'How are you',
   u'Is anyone there?',
   u'Hello',
   u'Good day'],
  u'tag': u'greeting'},
 {u'patterns': [u'Bye', u'See you later', u'Goodbye'], u'tag': u'goodbye'},
 {u'patterns': [u'Thanks', u'Thank you', u"That's helpful"],
  u'tag': u'thanks'},
 {u'patterns': [u'What hours are you open?',
   u'What are your hours?',
   u'When are you open?'],
  u'tag': u'hours'},
 {u'patterns': [u'Which mopeds do you have?',
   u'What kinds of mopeds are there?',
   u'What do you rent?'],
  u'tag': u'mopeds'},
 {u'patterns': [u'Do you take credit cards?',
   u'Do you accept Mastercard?',
   u'Are you cash only?'],
  u'tag': u'payments'},
 {u'patterns': [u'Are you open today?',
   u'When do you open today?',
   u'What are your hours today?'],
  u'tag': u'opentoday'},
 {u'patterns': [u'Can we rent a moped?',
   u"I'd like to rent a moped",
   u'How does this work?'],
  u'tag': u'rental'},
 {u'patterns': [u'today', u'Today'], u'tag': u'today'}]

In [61]:
def response_2(sentence, userID='123', show_details=False):
    
    results = classify(sentence)
    print "result probability"
    print results[0][1]
    if results[0][1] < 0.6:
        for i in dialog['dialog']:
            if i['triggered_by'][0] == "anything_else":
                return  i['response_by'][0] 
    else:   

    #print results
        if results:
            while results:
                for i in dialog['dialog']:
                    if i['triggered_by'][0]== results[0][0]:
                        return random.choice(i['response_by'])
                    print i  
    results.pop(0)

In [62]:
def locateByName(e,name):
    if e.get('tag',None) == name:
        return e

    for child in e.get('child_node',[]):
        result = locateByName(child,name)
        if result is not None:
            return result

    return None

In [63]:
dialog_input=dialog
locateByName(dialog_input,'asking_rental')['child_node']

[{u'child_node': [],
  u'child_status': False,
  u'jump_status': True,
  u'jump_to': u'main_node',
  u'response_by': [u'For rentals today please call 1-800-MYMOPED'],
  u'tag': u'today',
  u'triggered_by': [u'today']},
 {u'child_node': [],
  u'child_status': False,
  u'jump_status': True,
  u'jump_to': u'main_node',
  u'response_by': [u'For rentals today please call 1-800-MYMOPED'],
  u'tag': u'other_days',
  u'triggered_by': [u'not_today']},
 {u'child_node': [],
  u'child_status': False,
  u'jump_status': True,
  u'jump_to': u'main_node',
  u'response_by': [u'NOT RESPONSE'],
  u'tag': u'other_conversation',
  u'triggered_by': [u'greeting',
   u'goodbye',
   u'thanks',
   u'hours',
   u'mopeds',
   u'payments',
   u'opentoday',
   u'rental']}]

In [64]:
def response_3(sentence,dialog_input):
    results = classify(sentence)
    with open('dialog.json') as json_data:
                dialog_temp = json.load(json_data)

    
    if results[0][1] < 0.6:
        for i in dialog_input['child_node']:
            if i['triggered_by'][0] == "anything_else":
                return  i['response_by'][0],dialog_input 
    else:   
        if results:
            while results:
                for i in dialog_input['child_node']:
                    if i['triggered_by'][0]== results[0][0]:
                        state=1
                        if i['jump_status'] == True:
                            child_node=locateByName(dialog_temp,i['jump_to'])  
                        else:
                            child_node=i
                            
                        return random.choice(i['response_by']),child_node 
    results.pop(0)

In [65]:
dialog_input=dialog
output,dialog_input=response_3('Pika pou',dialog_input)
print "========================================="
print output
print "========================================="

Please be more explicit, I'm here to help you reserve you Moped


In [69]:
dialog_input=dialog

output,dialog_input=response_3('I would like to rent a moped',dialog_input)
print "========================================="
print 'Me:I would like to rent a moped'
print "========================================="
print "Bot:"+output
print "========================================="


output,dialog_input=response_3('Hi',dialog_input)
print "========================================="
print 'Me:Hi'
print "========================================="
print "Bot:"+output
print "========================================="
output,dialog_input=response_3('Hi',dialog_input)
print "========================================="
print "Bot:"+output
print "========================================="








output,dialog_input=response_3('do you take credit card',dialog_input)
print "========================================="
print 'Me:do you take credit card'
print "========================================="
print "Bot:"+output
print "========================================="
output,dialog_input=response_3('I would like to rent a moped',dialog_input)
print "========================================="
print 'Me:I would like to rent a moped'
print "========================================="
print "Bot:"+output
print "========================================="

Me:I would like to rent a moped
Bot:Are you looking to rent today or later this week?
Me:Hi
Bot:NOT RESPONSE
Bot:Good to see you again
Me:do you take credit card
Bot:We accept VISA, Mastercard and AMEX
Me:I would like to rent a moped
Bot:Are you looking to rent today or later this week?


In [43]:
classify('When are you open')

[(u'hours', 0.9513492)]

In [45]:
dialog_input

{u'child_node': [{u'child_node': [],
   u'child_status': False,
   u'jump_status': True,
   u'jump_to': u'main_node',
   u'response_by': [u'For rentals today please call 1-800-MYMOPED'],
   u'tag': u'today',
   u'triggered_by': [u'today']},
  {u'child_node': [],
   u'child_status': False,
   u'jump_status': True,
   u'jump_to': u'main_node',
   u'response_by': [u'For rentals today please call 1-800-MYMOPED'],
   u'tag': u'other_days',
   u'triggered_by': [u'not_today']}],
 u'child_status': True,
 u'jump_status': False,
 u'jump_to': u'',
 u'response_by': [u'Are you looking to rent today or later this week?'],
 u'tag': u'asking_rental',
 u'triggered_by': [u'rental']}

In [36]:
dialog_input


{u'child_node': [{u'child_node': [],
   u'child_status': False,
   u'jump_status': True,
   u'jump_to': u'main_node',
   u'response_by': [u'Hello thanks for visiting',
    u'Good to see you again',
    u'Hi there, how can I help?'],
   u'tag': u'conversation_start',
   u'triggered_by': [u'greeting']},
  {u'child_node': [],
   u'child_status': False,
   u'jump_status': True,
   u'jump_to': u'main_node',
   u'response_by': [u"We're open everyday 9am-9pm",
    u'Our hours are 9am - 9pm everyday'],
   u'tag': u'operating_time',
   u'triggered_by': [u'hours']},
  {u'child_node': [],
   u'child_status': False,
   u'jump_status': True,
   u'jump_to': u'main_node',
   u'response_by': [u'We rent Yamaha, Piaggio and Vespa mopeds',
    u'We have Piaggio,Vespa and Yamaha mopeds'],
   u'tag': u'asking_rental_rental_type',
   u'triggered_by': [u'mopeds']},
  {u'child_node': [{u'child_node': [],
     u'child_status': False,
     u'jump_status': True,
     u'jump_to': u'main_node',
     u'response_by'

In [30]:
dialog_input

{u'child_node': [],
 u'child_status': False,
 u'jump_status': True,
 u'jump_to': u'main_node',
 u'response_by': [u'For rentals today please call 1-800-MYMOPED'],
 u'tag': u'today',
 u'triggered_by': [u'today']}

In [66]:
output,dialog_tag,dialog_input_2=response_3('today','test',dialog_input)

test
result probability
today++++


TypeError: 'NoneType' object is not iterable

In [61]:
dialog_input

{u'child_node': [{u'child_node': [],
   u'child_status': False,
   u'jump_status': False,
   u'jump_to': u'',
   u'response_by': [u'Hello thanks for visiting',
    u'Good to see you again',
    u'Hi there, how can I help?'],
   u'tag': u'conversation_start',
   u'triggered_by': [u'greeting']},
  {u'child_node': [],
   u'child_status': False,
   u'jump_status': False,
   u'jump_to': u'',
   u'response_by': [u"We're open everyday 9am-9pm",
    u'Our hours are 9am - 9pm everyday'],
   u'tag': u'operating_time',
   u'triggered_by': [u'hours']},
  {u'child_node': [],
   u'child_status': False,
   u'jump_status': False,
   u'jump_to': u'',
   u'response_by': [u'We rent Yamaha, Piaggio and Vespa mopeds',
    u'We have Piaggio,Vespa and Yamaha mopeds'],
   u'tag': u'asking_rental_rental_type',
   u'triggered_by': [u'mopeds']},
  {u'child_node': [{u'child_node': [],
     u'child_status': False,
     u'jump_status': True,
     u'jump_to': u'main_node',
     u'response_by': [u'For rentals today p

In [57]:
dialog_input

{u'child_node': [{u'child_node': [],
   u'child_status': False,
   u'jump_status': False,
   u'jump_to': u'',
   u'response_by': [u'Hello thanks for visiting',
    u'Good to see you again',
    u'Hi there, how can I help?'],
   u'tag': u'conversation_start',
   u'triggered_by': [u'greeting']},
  {u'child_node': [],
   u'child_status': False,
   u'jump_status': False,
   u'jump_to': u'',
   u'response_by': [u"We're open everyday 9am-9pm",
    u'Our hours are 9am - 9pm everyday'],
   u'tag': u'operating_time',
   u'triggered_by': [u'hours']},
  {u'child_node': [],
   u'child_status': False,
   u'jump_status': False,
   u'jump_to': u'',
   u'response_by': [u'We rent Yamaha, Piaggio and Vespa mopeds',
    u'We have Piaggio,Vespa and Yamaha mopeds'],
   u'tag': u'asking_rental_rental_type',
   u'triggered_by': [u'mopeds']},
  {u'child_node': [{u'child_node': [],
     u'child_status': False,
     u'jump_status': True,
     u'jump_to': u'main_node',
     u'response_by': [u'For rentals today p

In [55]:
dialog_input['child_node']

[{u'child_node': [],
  u'child_status': False,
  u'jump_status': False,
  u'jump_to': u'',
  u'response_by': [u'Hello thanks for visiting',
   u'Good to see you again',
   u'Hi there, how can I help?'],
  u'tag': u'conversation_start',
  u'triggered_by': [u'greeting']},
 {u'child_node': [],
  u'child_status': False,
  u'jump_status': False,
  u'jump_to': u'',
  u'response_by': [u"We're open everyday 9am-9pm",
   u'Our hours are 9am - 9pm everyday'],
  u'tag': u'operating_time',
  u'triggered_by': [u'hours']},
 {u'child_node': [],
  u'child_status': False,
  u'jump_status': False,
  u'jump_to': u'',
  u'response_by': [u'We rent Yamaha, Piaggio and Vespa mopeds',
   u'We have Piaggio,Vespa and Yamaha mopeds'],
  u'tag': u'asking_rental_rental_type',
  u'triggered_by': [u'mopeds']},
 {u'child_node': [{u'child_node': [],
    u'child_status': False,
    u'jump_status': True,
    u'jump_to': u'main_node',
    u'response_by': [u'For rentals today please call 1-800-MYMOPED'],
    u'tag': u'tod

In [31]:
output,dialog_tag,dialog_input_2=response_3('Today',dialog_tag,dialog_input)
print output

asking_rental
result probability
today++++


TypeError: string indices must be integers

In [30]:
dialog_input['child_node']

[{u'child_node': [],
  u'child_status': False,
  u'jump_status': True,
  u'jump_to': u'main_node',
  u'response_by': [u'For rentals today please call 1-800-MYMOPED'],
  u'tag': u'today',
  u'triggered_by': [u'today']},
 {u'child_node': [],
  u'child_status': False,
  u'jump_status': True,
  u'jump_to': u'main_node',
  u'response_by': [u'For rentals today please call 1-800-MYMOPED'],
  u'tag': u'other_days',
  u'triggered_by': [u'not_today']}]

In [152]:
dialog_input

{u'child_node': [{u'child_node': [],
   u'child_status': False,
   u'jump_status': True,
   u'jump_to': u'main_node',
   u'response_by': [u'For rentals today please call 1-800-MYMOPED'],
   u'tag': u'today',
   u'triggered_by': [u'today']},
  {u'child_node': [],
   u'child_status': False,
   u'jump_status': True,
   u'jump_to': u'main_node',
   u'response_by': [u'For rentals today please call 1-800-MYMOPED'],
   u'tag': u'other_days',
   u'triggered_by': [u'not_today']}],
 u'child_status': True,
 u'jump_status': False,
 u'jump_to': u'',
 u'response_by': [u'Are you looking to rent today or later this week?'],
 u'tag': u'asking_rental',
 u'triggered_by': [u'rental']}

today
result probability
thanks++++
{u'jump_status': True, u'triggered_by': [u'today'], u'tag': u'today', u'child_node': [], u'response_by': [u'For rentals today please call 1-800-MYMOPED'], u'child_status': False, u'jump_to': u'main_node'}
{u'jump_status': True, u'triggered_by': [u'not_today'], u'tag': u'other_days', u'child_node': [], u'response_by': [u'For rentals today please call 1-800-MYMOPED'], u'child_status': False, u'jump_to': u'main_node'}
{u'jump_status': True, u'triggered_by': [u'today'], u'tag': u'today', u'child_node': [], u'response_by': [u'For rentals today please call 1-800-MYMOPED'], u'child_status': False, u'jump_to': u'main_node'}
{u'jump_status': True, u'triggered_by': [u'not_today'], u'tag': u'other_days', u'child_node': [], u'response_by': [u'For rentals today please call 1-800-MYMOPED'], u'child_status': False, u'jump_to': u'main_node'}
{u'jump_status': True, u'triggered_by': [u'today'], u'tag': u'today', u'child_node': [], u'response_by': [u'For rentals today 

In [20]:
dialog_input_2

[{u'child_node': [],
  u'child_status': False,
  u'response_by': [u'Hello thanks for visiting',
   u'Good to see you again',
   u'Hi there, how can I help?'],
  u'tag': u'conversation_start',
  u'triggered_by': [u'greeting']},
 {u'child_node': [],
  u'child_status': False,
  u'response_by': [u"We're open everyday 9am-9pm",
   u'Our hours are 9am - 9pm everyday'],
  u'tag': u'operating_time',
  u'triggered_by': [u'hours']},
 {u'child_node': [],
  u'child_status': False,
  u'response_by': [u'We rent Yamaha, Piaggio and Vespa mopeds',
   u'We have Piaggio,Vespa and Yamaha mopeds'],
  u'tag': u'asking_rental_rental_type',
  u'triggered_by': [u'mopeds']},
 {u'child_node': [{u'child_node': [],
    u'child_status': False,
    u'response_by': [u'For rentals today please call 1-800-MYMOPED'],
    u'tag': u'today',
    u'triggered_by': [u'today']},
   {u'child_node': [],
    u'child_status': False,
    u'response_by': [u'For rentals today please call 1-800-MYMOPED'],
    u'tag': u'other_days',
 

In [94]:
dialog_input

In [45]:
dialog['child_node']

[{u'child_node': [],
  u'child_status': False,
  u'response_by': [u'Hello thanks for visiting',
   u'Good to see you again',
   u'Hi there, how can I help?'],
  u'tag': u'conversation_start',
  u'triggered_by': [u'greeting']},
 {u'child_node': [],
  u'child_status': False,
  u'response_by': [u"We're open everyday 9am-9pm",
   u'Our hours are 9am - 9pm everyday'],
  u'tag': u'operating_time',
  u'triggered_by': [u'hours']},
 {u'child_node': [],
  u'child_status': False,
  u'response_by': [u'We rent Yamaha, Piaggio and Vespa mopeds',
   u'We have Piaggio,Vespa and Yamaha mopeds'],
  u'tag': u'asking_rental_rental_type',
  u'triggered_by': [u'mopeds']},
 {u'child_node': [{u'child_node': [],
    u'child_status': False,
    u'response_by': [u'For rentals today please call 1-800-MYMOPED'],
    u'tag': u'today',
    u'triggered_by': [u'today']},
   {u'child_node': [],
    u'child_status': False,
    u'response_by': [u'For rentals today please call 1-800-MYMOPED'],
    u'tag': u'other_days',
 